In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import pickle
import os
import decoupler as dc
from sklearn.metrics import roc_auc_score
from tqdm import tqdm
import re

%load_ext rpy2.ipython

In [63]:
%%R
suppressMessages({
    library(tidyverse)
    library(ggfortify)
    library(limma)
    library(cowplot)
    library(vsn)
    library(ggrepel)
})

In [72]:
coral_df = pd.read_csv('data/processed_data/coral_df.csv')

In [65]:
translator_df = pd.read_csv('data/processed_data/translator_df.csv')
uniprot_to_symbol = translator_df.set_index('uniprot')['symbol'].to_dict()
symbol_to_uniprot = translator_df.set_index('symbol')['uniprot'].to_dict()

In [66]:
cache_file = '/tmp/kinsubs.pkn'
if os.path.exists(cache_file):
    pkn = pickle.load(open(cache_file, 'rb'))
else:
    literature = pd.read_csv('data/processed_data/omnipath_enzsub.csv.gz')
    kinlibrary = pd.read_csv('data/processed_data/kinase_library.csv.gz')
    phosformer = pd.read_csv('data/processed_data/phosformer_preds.csv.gz')
    literature['resource'] = 'literature'
    literature['score'] = 1
    literature = literature[['source', 'target', 'score', 'resource', 'n_references']].drop_duplicates()
    cutoffs = {
        'Rigorous': (99, 0.8),
        'Moderate': (95, 0.65),
        'Relaxed': (90, 0.5)
    }
    dflist = [literature]
    for cutoff, (kinlib_cutoff, phosformer_cutoff) in cutoffs.items():
        kinfilt = kinlibrary[kinlibrary['score'] >= kinlib_cutoff].copy()
        kinfilt = kinfilt.groupby(['source', 'target']).agg({'score': 'max'}).reset_index()
        kinfilt['score'] = kinfilt['score'] / kinfilt['score'].max()
        kinfilt['resource'] = 'kinlibrary-' + cutoff
        dflist.append(kinfilt)
        phosfilt = phosformer[phosformer['score'] >= phosformer_cutoff].copy()
        phosfilt = phosfilt.groupby(['source', 'target']).agg({'score': 'max'}).reset_index()
        phosfilt['score'] = phosfilt['score'] / phosfilt['score'].max()
        phosfilt['resource'] = 'phosformer-' + cutoff
        dflist.append(phosfilt)
        comb = pd.concat([literature, phosfilt, kinfilt])
        comb = comb.loc[comb.groupby(['source', 'target'])['score'].idxmax()]
        comb = comb.drop_duplicates(subset=['source', 'target'])
        comb['resource'] = 'combined-' + cutoff
        dflist.append(comb)
    pkn = pd.concat(dflist)
    coral_kins = pd.read_csv('data/source_data/coral/coral_df.csv')
    human_kins = coral_kins['id.uniprot'].unique()
    pkn = pkn[pkn['source'].isin(human_kins)].copy()
    pickle.dump(pkn, open(cache_file, 'wb'))

In [37]:
toplot = pkn.groupby('resource').size().reset_index(name='count')

In [ ]:
%%R -i toplot -w 600 -h 400
int_cols <- c('no resource' = 'gray', 'literature'= '#fde725','kinlibrary'='#31688e', 'phosformer' = '#35b779', 'combined'='#440154')
threshold_rename <- c('literature' = 'literature', 'Rigorous' = 'Strict', 'Moderate' = 'Moderate', 'Relaxed' = 'Lenient')

p <- toplot %>%
    mutate(origin = str_replace(resource, '-.*', '')) %>%
    mutate(resource = fct_reorder(resource, count)) %>%
    ggplot(aes(x = resource, y = count, fill = origin, label = count)) +
    geom_bar(stat = 'identity') +
    scale_fill_manual(values = int_cols) +
    theme_minimal() +
    theme(axis.text.x = element_text(angle = 45, hjust = 1)) +
    labs(x = 'Resource', y = 'Number of interactions') +
    scale_x_discrete(labels = threshold_rename) +
    theme(legend.position = 'none') +
    theme_cowplot() +
    theme(axis.text.x = element_text(angle = 45, hjust = 1)) 
    
ggsave('figures/supp/pkn_counts.png', p, width = 8, height = 4)
p

In [39]:
hijazi_data = pd.read_csv('data/processed_data/hijazi_long.csv.gz')
hijazi_drug_to_kinase = pd.read_csv('data/processed_data/hijazi_drug_to_kinase.csv.gz')

In [40]:
lit_kinases = pkn[pkn['resource'] == 'literature']['source'].unique()
pkn_lit_kins = pkn[pkn['source'].isin(lit_kinases)].copy()

In [41]:
cache_file = '/tmp/kinase_activities.p'
if os.path.exists(cache_file):
    coverage_df, kinase_activities_df = pickle.load(open(cache_file, 'rb'))
else:
    coverage_l = []
    kinase_activities = []
    for cell in hijazi_data['cell'].unique():
        cell_data = hijazi_data[hijazi_data['cell'] == cell].copy()
        cell_sites = set(cell_data[cell_data['fold'] != 0]['site_id'])
        cell_to_dc = cell_data.pivot_table(index='drug', columns = 'site_id', values = 'fold')
        for resource in pkn['resource'].unique():
            resource_data = pkn[pkn['resource'] == resource].copy()
            resource_data['weight'] = resource_data['score']
            covered_sites = set(resource_data['target']).intersection(cell_sites)
            coverage_l.append({ 'cell': cell, 'resource': resource, 'total_sites': len(cell_sites), 'covered': len(covered_sites), 'proportion': len(covered_sites) / len(cell_sites) })
            kin_result = dc.dense_run(dc.run_ulm, net = resource_data, mat = cell_to_dc, verbose = True)
            dc_df = pd.DataFrame(kin_result[0].T).reset_index().melt(id_vars='index', var_name='drug', value_name='activity').rename(columns={'index': 'kinase'})
            dc_df['resource'] = resource
            dc_df['cell'] = cell
            kinase_activities.append(dc_df)

    coverage_df = pd.DataFrame(coverage_l)
    kinase_activities_df = pd.concat(kinase_activities)
    pickle.dump((coverage_df, kinase_activities_df), open('/tmp/kinase_activities.p', 'wb'))

In [42]:
kin_toevaluate = kinase_activities_df.merge(hijazi_drug_to_kinase, left_on = ['drug', 'kinase'], right_on = ['drug', 'kin_uniprot'], how = 'inner')
kin_toevaluate['count_per_cell'] = kin_toevaluate.groupby(['cell', 'kinase', 'drug'])['activity'].transform('count')

In [43]:
roc_res_df = []
for int_resource in kin_toevaluate['resource'].unique():
    for subset in ['all', 'common']:
        if subset =='all':
            kintoev = kin_toevaluate.copy()
        else:
            kintoev = kin_toevaluate[kin_toevaluate['count_per_cell'] == kin_toevaluate['resource'].nunique()].copy()
        resource_df = kintoev[kintoev['resource'] == int_resource].copy()
        resource_df['tp'] = resource_df['inhibition'] <= 0.5
        resource_df['tp'] = resource_df['tp'].astype(int)
        tp_df = resource_df[resource_df['tp'] == 1].copy()
        tn_df = resource_df[resource_df['tp'] == 0].copy()
        try:
            auroc_list = []
            for i in range(1000):
                tn_sample = tn_df.sample(n = len(tp_df), replace = False)
                toroc = pd.concat([tp_df, tn_sample]).dropna()
                roc_res = roc_auc_score(toroc['tp'], toroc['activity'] * -1)
                auroc_list.append(roc_res)
            roc_res_df.append({ 'resource': int_resource, 'AUROC': np.mean(auroc_list), 'subset': subset })
        except:
            print('Error with', int_resource, subset)
            pass
            
roc_res_df = pd.DataFrame(roc_res_df)

In [44]:
toplot = roc_res_df.merge(coverage_df, on = 'resource', how = 'inner')
toplot = toplot.groupby(['resource','subset']).agg({'AUROC': 'mean', 'proportion': 'mean'}).reset_index()
toplot.to_csv('/tmp/toplot.csv')

In [ ]:
%%R -w 650 -h 350
toplot <- read_csv('/tmp/toplot.csv')
int_cols <- c('no resource' = 'gray', 'literature'= '#fde725','kinlibrary'='#31688e', 'phosformer' = '#35b779', 'combined'='#440154')
threshold_rename <- c('literature' = 'literature', 'Rigorous' = 'Strict', 'Moderate' = 'Moderate', 'Relaxed' = 'Lenient')

p <- toplot %>%
  dplyr::mutate(origin = str_replace(resource, '-.*', '')) %>%
  dplyr::mutate(threshold = str_replace(resource, '.*-', '')) %>%
  mutate(threshold = threshold_rename[threshold]) %>%
  mutate(threshold = factor(threshold, levels = c('literature', 'Lenient', 'Moderate', 'Strict'))) %>%
  ggplot(aes(x = AUROC, y = proportion, label = resource, color = origin, shape = threshold)) +
  geom_point(size = 4) +
  facet_grid(cols = vars(subset)) +
  scale_color_manual(name = 'Resource', values = int_cols) +
  scale_shape_discrete(name = 'Threshold') +
  xlab('AUROC\n(Common kinases)') +
  ylab('Coverage\n(Proportion of quantified sites)') +
  theme_cowplot()

ggsave('figures/main/roc_hijazi.pdf', p, width = 9, height = 3.5, dpi = 300, bg = 'transparent')
p

In [68]:
kinlib_cutoff = 95
phosformer_cutoff = 0.65
cache_file = '/tmp/kinsubs_{}_{}.pkn'.format(kinlib_cutoff, phosformer_cutoff)
if os.path.exists(cache_file):
    pkn = pickle.load(open(cache_file, 'rb'))
else:
    literature = pd.read_csv('data/processed_data/omnipath_enzsub.csv.gz')
    kinlibrary = pd.read_csv('data/processed_data/kinase_library.csv.gz')
    phosformer = pd.read_csv('data/processed_data/phosformer_preds.csv.gz')
    kinlib_nints = kinlibrary.shape[0]
    phosformer_nints = phosformer.shape[0]
    literature = literature.groupby(['source', 'target']).agg({'n_references': 'max'}).reset_index()
    literature['resource'] = 'literature'
    literature['score'] = 1
    literature = literature[['source', 'target', 'score', 'resource', 'n_references']].drop_duplicates()
    kinlibrary = kinlibrary[kinlibrary['score'] >= kinlib_cutoff].copy()
    kinlib_filtins = kinlibrary.shape[0]
    print('Kinase library: {}% of interactions kept'.format(kinlib_filtins / kinlib_nints * 100))
    kinlibrary = kinlibrary.groupby(['source', 'target']).agg({'score': 'max'}).reset_index()
    kinlibrary['score'] = kinlibrary['score'] / kinlibrary['score'].max()
    kinlibrary['resource'] = 'kinlibrary'
    phosformer = phosformer[phosformer['score'] >= phosformer_cutoff].copy()
    phosformer_filtins = phosformer.shape[0]
    print('Phosformer: {}% of interactions kept'.format(phosformer_filtins / phosformer_nints * 100))
    phosformer = phosformer.groupby(['source', 'target']).agg({'score': 'max'}).reset_index()
    phosformer['resource'] = 'phosformer'
    phosformer['score'] = phosformer['score'] / phosformer['score'].max()
    pkn = pd.concat([literature, kinlibrary, phosformer])
    coral_kins = pd.read_csv('data/processed_data/coral/coral_df.csv')
    human_kins = coral_kins['id.uniprot'].unique()
    pkn = pkn[pkn['source'].isin(human_kins)].copy()
    pickle.dump(pkn, open(cache_file, 'wb'))
pkn = pkn.rename(columns = {'score': 'weight'})
pkn_all = pkn.groupby(['source', 'target']).agg({'weight': 'max'}).reset_index()
pkn_all['resource'] = 'combined'
pkn = pd.concat([pkn, pkn_all])

In [71]:
pkn.to_csv('supp_tables/1_kinsub_network.csv.gz', index = False, compression = 'gzip')

In [ ]:
print(pkn_all.shape[0])
print(pkn_all['target'].nunique())
print(pkn_all['source'].nunique())

In [ ]:
pkn.groupby('resource').agg({'weight': 'mean'})

In [49]:
color_map = {'no resource': 'gray', 'literature': '#fde725', 'kinlibrary': '#31688e','phosformer': '#35b779', 'combined': '#440154'}
toplot = pkn.groupby('resource').agg({'source': 'nunique', 'target': 'nunique', 'weight': 'count'}).reset_index().rename(columns = {'source': 'Kinases', 'target': 'Phosphosites', 'weight': 'Interactions'})
toplot = toplot.melt(id_vars = 'resource', var_name = 'Type', value_name = 'Count')
toplot.to_csv('/tmp/toplot.csv')

In [ ]:
%%R -w 600 -h 250 
toplot <- read_csv('/tmp/toplot.csv')
int_cols <- c('no resource' = 'gray', 'literature'= '#fde725', 'kinlibrary'='#31688e', 'phosformer' = '#35b779', 'combined'='#440154')

p <- toplot %>%
  mutate(Type = factor(Type, levels = c('Kinases', 'Phosphosites', 'Interactions'))) %>%
  mutate(resource = factor(resource, levels = c('no resource','literature',  'phosformer', 'kinlibrary', 'combined'))) %>%
  ggplot(aes(x = Count, y = resource, fill = resource)) +
  facet_grid(cols = vars(Type), scales = 'free_x') +
  scale_fill_manual(values = int_cols) +
  geom_bar(stat = 'identity', color = 'black', size = 0.5) +
  theme_cowplot() +
  theme(axis.text.x = element_text(angle = 45, hjust = 1)) +
  theme(legend.position = 'none') +
  theme(axis.title.y = element_blank()) 

ggsave('figures/main/coverage_kinome_barplot.pdf', p, width = 6, height = 2.5, dpi = 300, bg = 'transparent')
p

In [ ]:
tomean = pkn[pkn['resource'] == 'combined']
todistro = tomean.groupby(['source']).agg({'target': 'count'}).reset_index()
print(todistro['target'].mean())
print(todistro['target'].median())
print(todistro['target'].max())
todistro = pkn[pkn['resource'] != 'combined']
todistro = todistro.groupby(['source', 'resource']).agg({'target': 'count'}).reset_index()
todistro['proportion'] = todistro.groupby('resource')['target'].transform(lambda x: x / x.sum())
todistro.to_csv('/tmp/todistro.csv')

In [ ]:
%%R -w 600 -h 250
todistro <- read_csv('/tmp/todistro.csv')

p <- todistro %>%
    ggplot(aes(x = target, fill = resource)) +
    geom_histogram(alpha = 0.85, color = 'black', bins = 100) +
    scale_fill_manual(values = int_cols) +
    xlab('Number of interactions') +
    ylab('Density') +
    theme_cowplot()

ggsave('figures/supp/coverage_kinome_hist.png', p, width = 6, height = 2.5, dpi = 300, bg = 'transparent')
p

In [ ]:
pkn['id'] = pkn['source'] + '_' + pkn['target']
pkn['is_int'] = 1
pkn_bin = pkn.pivot_table(index='id', columns='resource', values='is_int').fillna(0).T
pkn_bin = pkn_bin.drop('combined')
intersection = pkn_bin.dot(pkn_bin.T)
set_size = pkn_bin.sum(axis=1)
min_size = pd.DataFrame(np.minimum(set_size.values[:, None], set_size.values[None, :]), 
                        index=set_size.index, columns=set_size.index)
overlap = intersection.div(min_size)
overlap_long = overlap.reset_index().melt(id_vars='resource', var_name='resource_2', value_name='overlap').dropna()
overlap_long.to_csv('/tmp/overlap_long.csv')
overlap_long

In [54]:
overlap_df = []
for int_resource in pkn['resource'].unique():
    pkn_bin = pkn[pkn['resource'] == int_resource].copy()
    pkn_bin['is_int'] = 1
    pkn_bin = pkn_bin.pivot_table(index='source', columns='target', values='is_int').fillna(0)
    intersection = pkn_bin.dot(pkn_bin.T)
    set_size = pkn_bin.sum(axis=1)
    min_size = pd.DataFrame(np.minimum(set_size.values[:, None], set_size.values[None, :]), 
                            index=set_size.index, columns=set_size.index)
    overlap = intersection.div(min_size)
    mask = np.triu(np.ones(overlap.shape)).astype(bool)
    overlap_masked = overlap.mask(mask)
    overlap_long = overlap_masked.reset_index().melt(id_vars='source', var_name='target', value_name='overlap').dropna()
    overlap_long['resource'] = int_resource
    overlap_df.append(overlap_long)
    
overlap_df = pd.concat(overlap_df)
overlap_df.to_csv('/tmp/overlap_df.csv')

In [ ]:
%%R -w 600 -h 250
toplot <- read_csv('/tmp/overlap_df.csv') 
p <- toplot %>%
  mutate(resource = factor(resource, levels = c('no resource','literature',  'phosformer', 'kinlibrary', 'combined'))) %>%
  mutate(resource = fct_reorder(resource, overlap)) %>%
  ggplot(aes(x = overlap, y = resource, fill = resource)) +
  geom_boxplot(outlier.shape = NA) +
  scale_fill_manual(values = int_cols) +
  theme_cowplot() +
  theme(legend.position = 'none') +
  xlab('Overlap Coefficient') +
  theme(axis.title.y = element_blank())
ggsave('figures/main/similarity.pdf', p, width = 3.5, height = 2.5, dpi = 300, bg = 'transparent')
p

In [56]:
toplot = pkn.copy()
toplot = toplot.groupby(['target', 'resource']).agg({'source': 'count'})
toplot = toplot.groupby('resource').agg({'source': lambda x: (x == 1).mean()}).reset_index()
toplot.to_csv('/tmp/toplot.csv')

In [ ]:
%%R -w 600 -h 250
toplot <- read_csv('/tmp/toplot.csv') 

p <- toplot %>%
  mutate(resource = fct_reorder(resource, source)) %>%
  ggplot(aes(y = resource, x = source, fill = resource)) +
  geom_col(color = 'black') + 
  scale_fill_manual(values = int_cols) +
  xlab('Sites with 1 interaction') +
  theme_cowplot() +
  theme(legend.position = 'none', axis.title.y = element_blank())
ggsave('figures/main/single_kinase.pdf', p, width = 3.5, height = 2.5, dpi = 300, bg = 'transparent')
p

In [58]:
tocoral = pkn.copy()
tocoral = tocoral[tocoral['resource'] != 'combined'].copy()
tocoral = tocoral.groupby(['source']).agg({'target': 'count', 'resource': lambda x: x.value_counts().index[0]}).reset_index()
from matplotlib.colors import to_hex
tocoral['kin_color'] = tocoral['resource'].apply(lambda x: to_hex(color_map[x]))
tocoral['kin_color'] = tocoral['kin_color'].str.upper()

In [59]:
literature_interactions = pkn[pkn['resource'] == 'literature'].copy()
lit_kins = literature_interactions.groupby('source').size().reset_index()
lit_kins = lit_kins.merge(coral_df, left_on='source', right_on='id.uniprot', how='left')

In [60]:
toplot_df = coral_df.merge(tocoral, left_on='id.uniprot', right_on='source', how='left')
toplot_df['node.col'] = toplot_df['kin_color']
toplot_df['node.col'] = toplot_df['node.col'].fillna('gray')
toplot_df['node.radius'] = toplot_df['target']
toplot_df['node.radius'] = np.interp(toplot_df['node.radius'], (toplot_df['node.radius'].min(), toplot_df['node.radius'].max()), (2, 7))
toplot_df['node.val.radius'] = toplot_df['node.radius']
toplot_df['text.label'] = ''
toplot_df.to_csv('/tmp/toplot.csv')

In [ ]:
%%R 
toplot_df <- read_csv('/tmp/toplot.csv')
source('other/minicoral/minicoral.R')
minval <- min(toplot_df$target, na.rm = TRUE)
maxval <- max(toplot_df$target, na.rm = TRUE)
minsize <- min(toplot_df$node.radius, na.rm = TRUE)
maxsize <- max(toplot_df$node.radius, na.rm = TRUE)
toplot_df$text.label <- ''
print(minsize, maxsize)
size_legend <- build.nodesize.legend(yoffset= 0, minval = minval, maxval = maxval, minsize = minsize, maxsize = maxsize)
writekinasetree(toplot_df, 'figures/main/kintree.svg', int_legend = size_legend[[1]])